In [1]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

2025-06-19 03:32:02.190129: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-06-19 03:32:02.196988: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-06-19 03:32:02.209463: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1750325522.227065   12014 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1750325522.232034   12014 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1750325522.251494   12014 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linkin

In [2]:
from tensorflow.keras.layers import Layer
import tensorflow.keras.backend as K

class FeatureWeightingLayer(Layer):
    def __init__(self, scaling_factors, **kwargs):
        super(FeatureWeightingLayer, self).__init__(**kwargs)
        self.scaling_factors = K.variable(scaling_factors, name='scaling_factors')

    def call(self, inputs):
        return inputs * self.scaling_factors

    def get_config(self):
        config = super(FeatureWeightingLayer, self).get_config()
        config.update({"scaling_factors": self.scaling_factors.numpy()})
        return config


In [3]:
import pandas as pd

# Define the path to your CSV file


# Define the column names
column_names = ['angle1', 'angle2', 'angle3', 'angle4', 'angle5', 'rolldeg', 'pitchdeg', 'anglegx', 'anglegy', 'anglegz', 'label']

# Read the CSV file into a DataFrame
df = pd.read_csv('dynamic_sensor_data_with_labels.csv', names=column_names)
                
print("Initial Data:")
print(df.head())

segments = []
current_segment = {'data': [], 'label': None}
segment_counts = {}  # Dictionary to track segment counts for each label
last_label = None  # Track the last label to reset segment count

for index, row in df.iterrows():
    # Check if the row indicates the start of a new segment
    if 'Start' in str(row['angle1']):
        if current_segment['data']:  # Complete the current segment before starting a new one
            segments.append(current_segment)
            label = current_segment['label']
            if label in segment_counts:
                segment_counts[label] += 1
            else:
                segment_counts[label] = 1
        current_segment = {'data': [], 'label': str(row['angle2']).strip()}  # Reset for new segment

    elif 'End' in str(row['angle1']):
        if current_segment['data']:  # Ensure there's data to conclude
            segments.append(current_segment)
            label = current_segment['label']
            if label not in segment_counts:
                segment_counts[label] = 1
            current_segment = {'data': [], 'label': None}

    else:
        current_segment['data'].append(row)

# Append the last segment if it hasn't been appended yet
if current_segment['data']:
    segments.append(current_segment)

print("\nNumber of Segments Captured:", len(segments))

# Iterate over segments and print each one's details
for segment in segments:
    label = segment['label']
    # Initialize segment count if it's the first time this label is being captured
    if label not in segment_counts:
        segment_counts[label] = 1
    # Convert segment data to DataFrame
    segment_df = pd.DataFrame(segment['data'])
    segment_df = segment_df.loc[:, ~segment_df.columns.duplicated()]
    # Print each segment's information with label-specific numbering
    print(f"\nSegment {segment_counts[label]} label: {label}, Data points: {len(segment['data'])}")
    print(segment_df.head())
    segment_counts[label] += 1  # Increment segment count for the label


Initial Data:
  angle1   angle2  angle3  angle4  angle5  rolldeg  pitchdeg  anglegx  \
0  Start     HOLA     NaN     NaN     NaN      NaN       NaN      NaN   
1   5.00  1687.00   680.0  1388.0   491.0   -24.98     -90.0    20.39   
2   1.00  1669.00   647.0  1387.0   485.0   -25.55     -90.0    20.45   
3   2.00  1675.00   647.0  1390.0   475.0   -23.44     -90.0    20.48   
4   2.00  1692.00   647.0  1380.0   487.0   -20.53     -90.0    20.49   

   anglegy  anglegz label  
0      NaN      NaN   NaN  
1    42.80     6.09  HOLA  
2    42.84     6.07  HOLA  
3    42.96     6.00  HOLA  
4    43.19     5.88  HOLA  

Number of Segments Captured: 320

Segment 1 label: HOLA, Data points: 101
  angle1   angle2  angle3  angle4  angle5  rolldeg  pitchdeg  anglegx  \
1   5.00  1687.00   680.0  1388.0   491.0   -24.98     -90.0    20.39   
2   1.00  1669.00   647.0  1387.0   485.0   -25.55     -90.0    20.45   
3   2.00  1675.00   647.0  1390.0   475.0   -23.44     -90.0    20.48   
4   2.00  16

In [4]:
# if 'Start' in str(row['angle1']):
#     if current_segment['data']:  # If current segment has data, save it before starting new
#         segments.append(current_segment)
#         print(f"Appending segment for label {current_segment['label']} with count {segment_counts[current_segment['label']]}")
#     current_segment = {'data': [], 'label': row['label']}
#     if row['label'] not in segment_counts:
#         segment_counts[row['label']] = 1  # Initialize or reset
#         print(f"New label detected: {row['label']}, starting count at {segment_counts[row['label']]}")
#     else:
#         segment_counts[row['label']] += 1

In [5]:
# Extract unique labels
unique_labels = set(segment['label'] for segment in segments)

# Print unique labels
print("Unique Labels:")
for label in unique_labels:
    print(label)


Unique Labels:
COMO_ESTAS
BIEN
SI
HOLA


In [6]:
# Convert the first two values in each data point to floats and remove the last column
for segment in segments:
    segment['data'] = [[float(value) if i < 2 else value for i, value in enumerate(data_point[:-1])] for data_point in segment['data']]


In [7]:
import numpy as np

# Extract unique labels
unique_labels = set(segment['label'] for segment in segments)

# Convert unique labels to a NumPy array
labels = np.array(list(unique_labels))

# Print unique labels array
print("Unique Labels Array:")
print(labels)


Unique Labels Array:
['COMO_ESTAS' 'BIEN' 'SI' 'HOLA']


In [8]:
# Print a sample segment
sample_segment = segments[0]  # Assuming you want to print the first segment
print(f"Segment label: {sample_segment['label']}")
print("Sample data points:")
for data_point in sample_segment['data']:  # Print the first 5 data points as a sample
    print(data_point)

Segment label: HOLA
Sample data points:
[5.0, 1687.0, 680.0, 1388.0, 491.0, -24.98, -90.0, 20.39, 42.8, 6.09]
[1.0, 1669.0, 647.0, 1387.0, 485.0, -25.55, -90.0, 20.45, 42.84, 6.07]
[2.0, 1675.0, 647.0, 1390.0, 475.0, -23.44, -90.0, 20.48, 42.96, 6.0]
[2.0, 1692.0, 647.0, 1380.0, 487.0, -20.53, -90.0, 20.49, 43.19, 5.88]
[4.0, 1675.0, 650.0, 1385.0, 485.0, -18.84, -90.0, 20.43, 43.45, 5.69]
[4.0, 1673.0, 663.0, 1385.0, 486.0, -23.04, -90.0, 20.23, 43.61, 5.35]
[3.0, 1669.0, 677.0, 1383.0, 487.0, -25.84, -90.0, 20.02, 43.77, 4.81]
[0.0, 1678.0, 685.0, 1379.0, 490.0, -15.5, -90.0, 20.06, 44.02, 4.11]
[5.0, 1659.0, 677.0, 1385.0, 487.0, -14.4, -90.0, 20.15, 44.14, 3.34]
[4.0, 1675.0, 681.0, 1383.0, 492.0, -14.07, -90.0, 20.09, 44.0, 2.53]
[1.0, 1669.0, 679.0, 1381.0, 493.0, -11.19, -90.0, 20.09, 43.68, 1.63]
[0.0, 1651.0, 677.0, 1384.0, 503.0, -9.01, -90.0, 20.13, 43.28, 0.74]
[4.0, 1687.0, 675.0, 1381.0, 489.0, -17.18, -90.0, 20.16, 42.78, -0.11]
[4.0, 1659.0, 687.0, 1381.0, 491.0, -13.52

In [9]:
# Assuming 'segments' is a list of dictionaries where each dictionary has a 'label' key

# Initialize a dictionary to count segments for each label
segments_count = {}

# Count the segments for each label
for segment in segments:
    label = segment['label']
    if label in segments_count:
        segments_count[label] += 1
    else:
        segments_count[label] = 1

# Print the total number of segments for each label
print("Total number of segments for each label:")
for label, count in segments_count.items():
    print(f"Label: {label}, Segments: {count}")


Total number of segments for each label:
Label: HOLA, Segments: 80
Label: BIEN, Segments: 80
Label: SI, Segments: 80
Label: COMO_ESTAS, Segments: 80


In [10]:
import numpy as np
import os

# Assuming 'segments' is defined as before
for segment in segments:
    # Create an array for each sample in the segment data
    segment['data'] = [np.array(sample) if not isinstance(sample, np.ndarray) else sample for sample in segment['data']]

# Now proceed with the rest of your code that depends on segment['data'] being an array
DATA_PATH = "/home/tonohn/LSTMSignLang/datacollection"  # Update this with your desired data path

for segment in segments:
    label = segment['label']
    segment_data = segment['data']

    # Create a folder for the label if it doesn't exist
    label_folder = os.path.join(DATA_PATH, label)
    if not os.path.exists(label_folder):
        os.makedirs(label_folder)

    # Find the next segment index for this label
    segment_index = len([name for name in os.listdir(label_folder) if os.path.isdir(os.path.join(label_folder, name))])

    # Create a folder for the new segment
    segment_folder = os.path.join(label_folder, f"segment_{segment_index}")
    if not os.path.exists(segment_folder):
        os.makedirs(segment_folder)

    # Save each sample in the segment as a separate .npy file
    for sample_index, sample_data in enumerate(segment_data):
        np.save(os.path.join(segment_folder, f"sample_{sample_index}.npy"), sample_data)


In [11]:
# Assuming 'segments' is a list of dictionaries where each dictionary has a 'label' and 'data' key
for segment in segments:
    print(f"Label: {segment['label']}")
    for sample_index, sample in enumerate(segment['data']):
        print(f"Sample {sample_index}: {sample}")


Label: HOLA
Sample 0: [   5.   1687.    680.   1388.    491.    -24.98  -90.     20.39   42.8
    6.09]
Sample 1: [ 1.000e+00  1.669e+03  6.470e+02  1.387e+03  4.850e+02 -2.555e+01
 -9.000e+01  2.045e+01  4.284e+01  6.070e+00]
Sample 2: [   2.   1675.    647.   1390.    475.    -23.44  -90.     20.48   42.96
    6.  ]
Sample 3: [   2.   1692.    647.   1380.    487.    -20.53  -90.     20.49   43.19
    5.88]
Sample 4: [   4.   1675.    650.   1385.    485.    -18.84  -90.     20.43   43.45
    5.69]
Sample 5: [   4.   1673.    663.   1385.    486.    -23.04  -90.     20.23   43.61
    5.35]
Sample 6: [   3.   1669.    677.   1383.    487.    -25.84  -90.     20.02   43.77
    4.81]
Sample 7: [   0.   1678.    685.   1379.    490.    -15.5   -90.     20.06   44.02
    4.11]
Sample 8: [   5.   1659.    677.   1385.    487.    -14.4   -90.     20.15   44.14
    3.34]
Sample 9: [   4.   1675.    681.   1383.    492.    -14.07  -90.     20.09   44.
    2.53]
Sample 10: [ 1.000e+00  1.669e+

In [12]:
from sklearn.model_selection import train_test_split
from tensorflow.keras.utils import to_categorical

In [13]:
actions = {seg['label'] for seg in segments}

# Create a mapping from label to a unique integer
label_map = {label: num for num, label in enumerate(actions)}

label_map

{'COMO_ESTAS': 0, 'BIEN': 1, 'SI': 2, 'HOLA': 3}

In [14]:
import numpy as np
import os

# Define your base data path where segments are stored
DATA_PATH = "/home/tonohn/LSTMSignLang/datacollection"
sequences = []
labels = []

# Assuming you have label_map defined somewhere
num_sequences_to_take = 79
num_samples_per_sequence = 68

for action in actions:
    label_folder = os.path.join(DATA_PATH, action)
    sequence_count = len([name for name in os.listdir(label_folder) if os.path.isdir(os.path.join(label_folder, name))])
    
    for sequence in range(min(sequence_count, num_sequences_to_take)):
        window = []
        sequence_path = os.path.join(label_folder, f"segment_{sequence}")
        frame_count = len([name for name in os.listdir(sequence_path) if name.endswith('.npy')])
        
        # FIX: Always sample exactly num_samples_per_sequence frames
        if frame_count >= num_samples_per_sequence:
            # If we have enough frames, sample without replacement
            sampled_frame_indices = np.random.choice(frame_count, size=num_samples_per_sequence, replace=False)
        else:
            # If we don't have enough frames, sample with replacement to reach target size
            sampled_frame_indices = np.random.choice(frame_count, size=num_samples_per_sequence, replace=True)
        
        # Sort indices to maintain temporal order (optional but recommended)
        sampled_frame_indices = np.sort(sampled_frame_indices)
        
        for frame_num in sampled_frame_indices:
            file_path = os.path.join(sequence_path, f"sample_{frame_num}.npy")
            res = np.load(file_path)
            window.append(res)
        
        sequences.append(window)
        labels.append(label_map[action])

# Now all sequences should have exactly num_samples_per_sequence frames
print(f"Number of sequences: {len(sequences)}")
print(f"Expected sequence length: {num_samples_per_sequence}")

# Verify all sequences have the same length
sequence_lengths = [len(seq) for seq in sequences]
print(f"Actual sequence lengths - Min: {min(sequence_lengths)}, Max: {max(sequence_lengths)}")

if len(set(sequence_lengths)) == 1:
    print("✓ All sequences have the same length!")
    # Convert to numpy arrays
    sequences = np.array(sequences)
    labels = np.array(labels)
    print(f"Sequences shape: {sequences.shape}")
    print(f"Labels shape: {labels.shape}")
else:
    print("✗ Sequences have different lengths")
    print("Sequence length distribution:", dict(zip(*np.unique(sequence_lengths, return_counts=True))))


Number of sequences: 316
Expected sequence length: 68
Actual sequence lengths - Min: 68, Max: 68
✓ All sequences have the same length!
Sequences shape: (316, 68, 10)
Labels shape: (316,)


In [15]:
#meaning we have 148 "videos"
labels.shape

(316,)

In [16]:
X = np.array(sequences)
X.shape

(316, 68, 10)

In [17]:
#converted labels to categorical
y = to_categorical(labels).astype(int)
y

array([[1, 0, 0, 0],
       [1, 0, 0, 0],
       [1, 0, 0, 0],
       ...,
       [0, 0, 0, 1],
       [0, 0, 0, 1],
       [0, 0, 0, 1]])

In [18]:
#splitting the date with 5% for testing

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.05)

In [19]:
X_train.shape

(300, 68, 10)

In [20]:
X_test.shape

(16, 68, 10)

### **TRAIN LSTM MODEL**

In [21]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard

In [22]:
log_dir = os.path.join('Logs')
tb_callback = TensorBoard(log_dir=log_dir)

In [23]:
# labels = pd.DataFrame(list(labels))
# labels
actions

{'BIEN', 'COMO_ESTAS', 'HOLA', 'SI'}

In [24]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.optimizers import Adam
import numpy as np

# Define your feature scaling factors: Increase the first five features' importance
scaling_factors = np.ones((10,))
scaling_factors[:5] = 10  # Scale up the first five features

In [25]:
model = Sequential([
    FeatureWeightingLayer(scaling_factors=scaling_factors, input_shape=(68, 10)),
    LSTM(64, return_sequences=True, activation='tanh'),
    LSTM(128, return_sequences=True, activation='tanh'),
    LSTM(64, return_sequences=False, activation='tanh'),
    Dense(64, activation='tanh'),
    Dense(32, activation='tanh'),
    Dense(len(np.unique(labels)), activation='softmax')  # Ensure `labels` is correctly defined
])

/tmp/ipykernel_12014/4237357604.py:6: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super(FeatureWeightingLayer, self).__init__(**kwargs)
E0000 00:00:1750325641.757245   12014 cuda_executor.cc:1228] INTERNAL: CUDA Runtime error: Failed call to cudaGetRuntimeVersion: Error loading CUDA libraries. GPU will not be used.: Error loading CUDA libraries. GPU will not be used.
W0000 00:00:1750325641.764433   12014 gpu_device.cc:2341] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


In [26]:
from tensorflow.keras.optimizers import Adam

# Compile the model
opt = Adam(learning_rate=0.0001)
model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['categorical_accuracy'])


In [27]:
# import pandas as pd

# # Check for null values in X_train
# nulls_in_X_train = np.isnan(X_train).sum()
# print("Null values in X_train:")
# print(nulls_in_X_train)

# # Check for null values in y_train
# nulls_in_y_train = np.isnan(y_train).sum()
# print("\nNull values in y_train:")
# print(nulls_in_y_train)


import numpy as np

# Check for NaN values in X_train
nan_values_in_X_train = np.isnan(X_train).sum()
print("NaN values in X_train:", nan_values_in_X_train)

# Check for infinity values in X_train
inf_values_in_X_train = np.isinf(X_train).sum()
print("Infinity values in X_train:", inf_values_in_X_train)

# Check for NaN values in y_train
nan_values_in_y_train = np.isnan(y_train).sum()
print("NaN values in y_train:", nan_values_in_y_train)

# Check for infinity values in y_train
inf_values_in_y_train = np.isinf(y_train).sum()
print("Infinity values in y_train:", inf_values_in_y_train)


NaN values in X_train: 0
Infinity values in X_train: 0
NaN values in y_train: 0
Infinity values in y_train: 0


In [28]:
model.fit(X_train, y_train, epochs=20, callbacks=[tb_callback])

Epoch 1/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 4s 116ms/step - categorical_accuracy: 0.3242 - loss: 1.4122
Epoch 2/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 99ms/step - categorical_accuracy: 0.7092 - loss: 1.2515
Epoch 3/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 100ms/step - categorical_accuracy: 0.7567 - loss: 1.1151
Epoch 4/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 100ms/step - categorical_accuracy: 0.7993 - loss: 0.9744
Epoch 5/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 100ms/step - categorical_accuracy: 0.8548 - loss: 0.7801
Epoch 6/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 103ms/step - categorical_accuracy: 0.8623 - loss: 0.6379
Epoch 7/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 101ms/step - categorical_accuracy: 0.9300 - loss: 0.4991
Epoch 8/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 100ms/step - categorical_accuracy: 0.9600 - loss: 0.3775
Epoch 9/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 106ms/step - categorical_accuracy: 0.9991 - loss: 0.2525
Epoch 10/20
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 102ms/step - categorical_accuracy: 0.9966 - loss: 0.1652
Epoch 11/20
10/10 ━━

In [29]:
model.summary()


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ feature_weighting_layer         │ (None, 68, 10)         │             0 │
│ (FeatureWeightingLayer)         │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm (LSTM)                     │ (None, 68, 64)         │        19,200 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 68, 128)        │        98,816 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_2 (LSTM)                   │ (None, 64)             │        49,408 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 64)             │         4,160 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 32)             │         2,080 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 4)              │           132 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 521,390 (1.99 MB)

 Trainable params: 173,796 (678.89 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 347,594 (1.33 MB)

In [30]:
res = model.predict(X_test)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 283ms/step


In [31]:
# Convert the set 'actions' to a list
actions_list = list(actions)

# Access the element using the index returned by np.argmax(res[0])
predicted_index = np.argmax(res[4])
predicted_action = actions_list[predicted_index]

print("Predicted action:", predicted_action)


Predicted action: COMO_ESTAS


In [32]:
predicted_index = np.argmax(y_test[4])
predicted_action = actions_list[predicted_index]

print("Predicted label:", predicted_action)

Predicted label: COMO_ESTAS


# **EVALUATION**

In [33]:
from sklearn.metrics import multilabel_confusion_matrix, accuracy_score


In [34]:
yhat = model.predict(X_test)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step


In [35]:
ytrue = np.argmax(y_test, axis=1).tolist()
yhat = np.argmax(yhat, axis=1).tolist()

In [36]:
multilabel_confusion_matrix(ytrue, yhat)

array([[[11,  0],
        [ 0,  5]],

       [[10,  0],
        [ 0,  6]],

       [[13,  0],
        [ 0,  3]],

       [[14,  0],
        [ 0,  2]]])

In [37]:
accuracy_score(ytrue, yhat)

1.0

In [38]:
# Assuming 'model' is your trained Keras model
model.save('modelo.h5')  # Saves the entire model to a single HDF5 file


In [39]:
from tensorflow.keras.models import load_model

# Assuming FeatureWeightingLayer is defined as shown above
custom_objects = {'FeatureWeightingLayer': FeatureWeightingLayer}

# Load the entire model back
model = load_model('modelo.h5', custom_objects=custom_objects)


In [40]:
res = model.predict(X_test)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 301ms/step


In [41]:
actions_list = list(actions)

# Access the element using the index returned by np.argmax(res[0])
predicted_index = np.argmax(res[4])
predicted_action = actions_list[predicted_index]

print("Predicted action:", predicted_action)

Predicted action: COMO_ESTAS


In [42]:
predicted_index = np.argmax(y_test[4])
predicted_action = actions_list[predicted_index]

print("Predicted label:", predicted_action)

Predicted label: COMO_ESTAS
